In [9]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint
import tensorflow as tf
import joblib

In [10]:
merged = pd.read_csv(r'../data/long_merge.csv')

In [11]:
zones = [69, 68, 67, 66, 65, 64, 42, 41, 40, 39, 38, 37, 36]
rtu = 1
cols = []

for zone in zones:
    for column in merged.columns:
        if (
            f"zone_0{zone}" in column
            and "co2" not in column
            and "hw_valve" not in column
            and "cooling_sp" not in column
            and "heating_sp" not in column
        ):
            cols.append(column)

cols = (
    ["date"]
    + cols
    + [
        f"rtu_00{rtu}_fltrd_sa_flow_tn",
        f"rtu_00{rtu}_sa_temp", 
        "air_temp_set_1",
        "air_temp_set_2",
        "dew_point_temperature_set_1d",
        "relative_humidity_set_1",
        "solar_radiation_set_1",
    ]
)

for zone in zones:
    for column in merged.columns:
        if f"zone_0{zone}" in column:
            if "cooling_sp" in column or "heating_sp" in column:
                cols.append(column)
                
input_dataset = merged[cols]

In [12]:
input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = input_dataset[ (input_dataset.date.dt.date >date(2019, 1, 1)) & (input_dataset.date.dt.date< date(2021, 1, 1))]

if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

C:\Users\arbal\AppData\Local\Temp\ipykernel_368\4293840618.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")


There are NA values in the DataFrame columns.


In [13]:
testdataset_df = df_filtered[(df_filtered.date.dt.date >date(2020, 3, 1)) & (df_filtered.date.dt.date <date(2020,7, 1))]

# traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

traindataset_df = df_filtered[(df_filtered.date.dt.date >date(2019, 3, 1)) & (df_filtered.date.dt.date <date(2020, 3, 1)) | (df_filtered.date.dt.date >date(2020, 7, 1)) & (df_filtered.date.dt.date <date(2020, 12, 1))]
testdataset = testdataset_df.drop(columns=["date"]).values
traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [14]:
traindataset_df.columns

Index(['date', 'zone_069_temp', 'zone_069_fan_spd', 'zone_068_temp',
       'zone_068_fan_spd', 'zone_067_temp', 'zone_067_fan_spd',
       'zone_066_temp', 'zone_066_fan_spd', 'zone_065_temp',
       'zone_065_fan_spd', 'zone_064_temp', 'zone_064_fan_spd',
       'zone_042_temp', 'zone_042_fan_spd', 'zone_041_temp',
       'zone_041_fan_spd', 'zone_040_temp', 'zone_040_fan_spd',
       'zone_039_temp', 'zone_039_fan_spd', 'zone_038_temp',
       'zone_038_fan_spd', 'zone_037_temp', 'zone_037_fan_spd',
       'zone_036_temp', 'zone_036_fan_spd', 'rtu_001_fltrd_sa_flow_tn',
       'rtu_001_sa_temp', 'air_temp_set_1', 'air_temp_set_2',
       'dew_point_temperature_set_1d', 'relative_humidity_set_1',
       'solar_radiation_set_1', 'zone_069_cooling_sp', 'zone_069_heating_sp',
       'zone_067_cooling_sp', 'zone_067_heating_sp', 'zone_066_cooling_sp',
       'zone_066_heating_sp', 'zone_065_cooling_sp', 'zone_065_heating_sp',
       'zone_064_cooling_sp', 'zone_064_heating_sp', 'zone_042

In [15]:
print(traindataset_df.isna().sum().sum(), testdataset_df.isna().sum().sum())

0 0


In [16]:
len(traindataset), len(testdataset)

(1073512, 391818)

In [18]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = StandardScaler()
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

joblib.dump(scaler, 'scaler_vav_1.pkl')

['scaler_vav_1.pkl']

In [10]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = []
    Y = []
    for i in range(len(dataset) - time_step - 1):
        x.append(dataset[i:(i+time_step),:])
        Y.append(dataset[i+time_step,0:26])
    x= np.array(x)
    Y = np.array(Y)
    return x,Y
time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)



In [ ]:
X_train.shape, y_train.shape

((1073481, 30, 55), (1073481, 26))

In [ ]:

model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=y_train.shape[1]))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_vav_01.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
# model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=3, batch_size=128, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/3
8387/8387 ━━━━━━━━━━━━━━━━━━━━ 0s 58ms/step - loss: 0.0696
Epoch 1: val_loss improved from inf to 0.65445, saving model to lstm_vav_01.keras
8387/8387 ━━━━━━━━━━━━━━━━━━━━ 589s 69ms/step - loss: 0.0696 - val_loss: 0.6544
Epoch 2/3
 449/8387 ━━━━━━━━━━━━━━━━━━━━ 7:16 55ms/step - loss: 0.0033

KeyboardInterrupt: 

In [13]:
import keras
checkpoint_path = "lstm_vav_01.keras"

model = keras.models.load_model(checkpoint_path)

In [55]:
model.load_weights(checkpoint_path)

In [56]:
test_predict1 = model.predict(X_test)

12244/12244 ━━━━━━━━━━━━━━━━━━━━ 110s 9ms/step


In [60]:
idx_to_col = {i:col for i,col in enumerate(traindataset_df.drop(columns = ['date']).columns)}
idx_to_col

{0: 'zone_069_temp',
 1: 'zone_069_fan_spd',
 2: 'zone_068_temp',
 3: 'zone_068_fan_spd',
 4: 'zone_067_temp',
 5: 'zone_067_fan_spd',
 6: 'zone_066_temp',
 7: 'zone_066_fan_spd',
 8: 'zone_065_temp',
 9: 'zone_065_fan_spd',
 10: 'zone_064_temp',
 11: 'zone_064_fan_spd',
 12: 'zone_042_temp',
 13: 'zone_042_fan_spd',
 14: 'zone_041_temp',
 15: 'zone_041_fan_spd',
 16: 'zone_040_temp',
 17: 'zone_040_fan_spd',
 18: 'zone_039_temp',
 19: 'zone_039_fan_spd',
 20: 'zone_038_temp',
 21: 'zone_038_fan_spd',
 22: 'zone_037_temp',
 23: 'zone_037_fan_spd',
 24: 'zone_036_temp',
 25: 'zone_036_fan_spd',
 26: 'rtu_001_fltrd_sa_flow_tn',
 27: 'rtu_001_sa_temp',
 28: 'air_temp_set_1',
 29: 'air_temp_set_2',
 30: 'dew_point_temperature_set_1d',
 31: 'relative_humidity_set_1',
 32: 'solar_radiation_set_1',
 33: 'zone_069_cooling_sp',
 34: 'zone_069_heating_sp',
 35: 'zone_067_cooling_sp',
 36: 'zone_067_heating_sp',
 37: 'zone_066_cooling_sp',
 38: 'zone_066_heating_sp',
 39: 'zone_065_cooling_sp',
 

In [ ]:
test_predict1_unscaled = test_predict1*scaler.scale_[0:31] + scaler.mean_[0:31]
y_test_unscaled = y_test*scaler.scale_[0:31] + scaler.mean_[0:31]

In [84]:
%matplotlib inline
var = 0

df = pd.DataFrame([testdataset_df.index[31:],test_predict1_unscaled[:,var], y_test_unscaled[:,var]] ).T
fig, ax = plt.subplots(figsize=(10,8))
df.plot(x = 0, y=1, ax = ax, label = 'Predicted')
df.plot(x = 0, y=2, ax = ax, label = 'Actual')

anomalies = df.where(df[1]-df[2]>0.38)[0]
df['anomalies'] = anomalies

df_new = df.dropna()

df_new.plot.scatter(x='anomalies', y=1,  c='r', ax = ax, label = 'Anomalies')

# ax.scatter(anomalies,test_predict1[anomalies,var], color='black',marker ="o",s=100 )


ax.set_title('Testing Data - Predicted vs Actual [Zone 72 Temperature]', fontsize=20)
ax.set_xlabel('Time', fontsize=15)
ax.set_ylabel('Value', fontsize = 15)
ax.legend(fontsize = 15)
fig.tight_layout()

In [18]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA


# Generating random data for demonstration
np.random.seed(0)
X =  test_predict1 - y_test


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2)

# Fitting the model to the data
gmm.fit(X)

# Getting the cluster labels
labels = gmm.predict(X)

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [86]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = (test_predict1 - y_test)

k = 2

pca = PCA(n_components=2)
X = pca.fit_transform(X)

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
# centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.text(centroids[0,0]+0.2, centroids[0,1]+0.5, 'Normal', fontsize=12, color='red')
plt.text(centroids[1,0]+0.5, centroids[1,1]+0.2, 'Anomaly', fontsize=12, color='red')
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.tight_layout()

joblib.dump(kmeans, 'kmeans_vav_2.pkl')
joblib.dump(pca, 'pca_vav_2.pkl')

['kmeans_vav_1.pkl']

In [19]:
k = 60
X= test_predict1 - y_test
processed_data = []
feat_df = pd.DataFrame(columns=["mean","std",])
for i in range(0,len(X), 60):
    mean = X[i:i+k].mean(axis = 0)
    std = X[i:i+k].std(axis = 0)
    max = X[i:i+k].max(axis = 0)
    min = X[i:i+k].min(axis = 0)
    iqr = np.percentile(X[i:i+k], 75, axis=0) - np.percentile(X[i:i+k], 25,axis=0)
    data = np.concatenate([mean, std, max, min, iqr])
    processed_data.append([data])
processed_data = np.concatenate(processed_data,axis=0) 

In [ ]:
X = processed_data

kmeans = KMeans(n_clusters=3, algorithm='elkan', max_iter=1000, n_init = 5)

kmeans.fit(X)

pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [21]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = processed_data

# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2, init_params='k-means++')

# Fitting the model to the data
gmm.fit(X)
labels = gmm.predict(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster labels

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()



In [38]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
# Generating random data for demonstration
np.random.seed(0)
X = test_predict1 - y_test 

kmeans = KMeans(n_clusters=2)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.figure()
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.text(centroids[0,0], centroids[0,1], 'Normal', fontsize=12, color='red')
plt.text(centroids[1,0], centroids[1,1], 'Anomaly', fontsize=12, color='red')
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [29]:
sum(labels==0)

329810